SAS & HSE, Applied Time Series Forecasitng , Fall 2024

<font color="green"> HW #1 </font>

<span style="color:black; font-size: 12pt"></span>

You can find hw1 bonus part <a href= "https://github.com/aromanenko/ATSF/blob/main/HW1_bonus_part.ipynb">here</a>

Alexey Romanenko,
<font color="blue">alexromsput@gmail.com</font>


<h1 align="center">Organization Info</h1>

**Дополнительный материал для выполнения дз**:
- Лукашин Ю.П. Адаптивные методы краткосрочного прогнозирования временных рядов. Финансы и статистика. 2003, главы 1,4,5,7.
- https://otexts.com/fpp2/expsmooth.html

**Оформление дз**:
- Присылайте выполненное задание anytask
- Выполненное дз сохраните в файл <Surname>_ts2024_25_hw1.ipynb, например, ivanov_ts2024_25_hw1.ipynb

**Вопросы**:
- Присылайте вопросы в телеграм в соответствующий канал

**Deadilne**: <font color="red"> 01-Dec-2024 11:59:59 pm CET </font>

В случае присланного решения позже дедлайна максимальный бал буде снижен согласно формуле (-1 балл за просрочку дедлайна в одну неделю):

$$МаксимальныйБалл=max\bigl(6,(10-ДнейПослеДедлайна/7) \bigr).$$
График зависимости максимально возможного балла за ДЗ от просрочки дедлайна приведён ниже:

In [1]:
import pandas as pd
import numpy as np
import datetime
pd.options.plotting.backend = "plotly"
deadline_dttm = pd.to_datetime('2024-12-01 00:00:00')

pd.DataFrame(data = [[deadline_dttm+datetime.timedelta(days=x)
                          , min(10, max(6, (10-x/7)))] for x in np.linspace(-4,30,35000)],
                          columns = ['Время сдачи ДЗ', 'Максимальный балл']).set_index('Время сдачи ДЗ').\
  plot().update_layout(height=350, width=1350).show()

<h1 align="center">Check Questions (5%)</h1>

Ответе на вопросы своими словами (загугленный материал надо пересказать), ответ обоснуйте (напишите и ОБЪЯСНИТЕ формулки если потребуется), если не выходит, то вернитесь к лекции дополнительным материалам:

**Вопрос 1**: Опишите, как изменяется адаптивная способность алгоритма Simple Exponential Smoothing при изменении параметра $\alpha$ от 0 до 1.

$\alpha$ корректирует прогноз. 

Изменение $\alpha$ меняет скорость увелчения прогноза.

**Вопрос 2**: Докажите равенство выражений в $\color{green}{рекуррентной~форме}$ и в $\color{red} {форме~корректировки~на~ошибку}$ для модели Тейла-Вейджа.

$$ \hat y_{t+d} = \hat l_t + \hat b_t\cdot d + \hat s_{t+(d\mod p)-p}. $$

$$ \hat l_t =  \color{green}{\alpha (y_t - \hat s_{t-p}) + (1-\alpha) (\hat l_{t-1} + \hat b_{t-1} )}=\color{red}{\hat l_{t-1} + \hat b_{t-1} + \alpha e_t};$$

$$\hat b_t =  \color{green}{\beta (\hat l_{t} - \hat l_{t-1} ) + (1-\beta) \hat b_{t-1} } = \color{red}{\hat b_{t-1} + \alpha\beta e_t};$$

$$ \hat s_t = \color{green}{\gamma (y_t-\hat l_{t}) + (1-\gamma) \hat s_{t-p} }= \color{red}{\hat s_{t-p} + \gamma(1-\alpha)e_t}.$$

где
$e_t = y_t-\hat y_t$


<Ответ>

**Вопрос 3**: Каким следует выбрать параметр сглаживания тренда $\beta$ в модели Хольта (линейный тренд) в случае, когда вы предсказываете временной ряд 1) с плавно меняющимя трендом; 2) стохастически меняющися трендом?

<Ответ>


<h1 align="center"> Practice</h1>

#1. reading data (5%)


In [6]:
# put you name and surname here
name_surname = 'luka_markov' # example 'ivan_ivanov'

ts_number = sum([ord(l) for l in name_surname])//73
print('Your ts number for HW1 is', ts_number)

Your ts number for HW1 is 16



<span style="color:blue; font-family:'New Times Roman'; font-size:14pt"> Find your ts <a href = 'https://docs.google.com/spreadsheets/d/1vQrQ5Ea9Mtouxff87ZcMK2CkoDXbXHKqOkAOTgdU454/edit?gid=0#gid=0'>here</a> in sheet "HW1" and download time series data


In [36]:
!pip3 install pandas
!pip3 install scipy
!pip3 install plotly
!pip3 install requests
!pip3 install --upgrade nbformat
!pip install ipykernel

zsh:1: command not found: pip


In [1]:
# start with this code
import requests
import io
import pandas as pd
import numpy as np
from utils import InitExponentialSmoothing, build_forecast, plot_ts_forecast
from utils import qualityMAPE

import plotly.graph_objects as go
import plotly.express as px
from plotly.subplots import make_subplots
pd.options.plotting.backend = "plotly"


# ts = pd.read_csv('???/mothly_ts.csv', sep=???, decimal=???, index_col=???, parse_dates=True, dayfirst=True)

# # Put your code below
# ts.plot().update_layout(height=350, width=1350).show()

url = 'https://raw.githubusercontent.com/aromanenko/ATSF/main/data/energy_consumption.csv'
response = requests.get(url)
content = response.content

df = pd.read_csv(io.StringIO(content.decode('utf-8')), parse_dates=['Date'])
ts = df[df.id == 0].drop(columns='id').set_index('Date')['2011-01-01':'2014-01-01']

In [2]:
df.head()

Date  EnergyConsumption  Temp1  Temp2  Temp3  Temp4  Temp5  Temp6  \
0 2010-01-01         147487.171  -17.8  -16.9    NaN    NaN    NaN    NaN   
1 2010-01-02         155433.800  -17.8  -20.3    NaN    NaN    NaN    NaN   
2 2010-01-03         164140.232  -16.4  -24.0    NaN    NaN    NaN    NaN   
3 2010-01-04         171382.848  -10.2  -15.7    NaN    NaN    NaN    NaN   
4 2010-01-05         170188.290   -7.2   -8.8    NaN    NaN    NaN    NaN   

   Temp7  Saturday  Sunday  Temp1_South_Less  Temp2_South_Less  \
0    NaN       0.0     1.0               NaN               NaN   
1    NaN       1.0     0.0               NaN               NaN   
2    NaN       0.0     1.0               NaN               NaN   
3    NaN       0.0     1.0               NaN               NaN   
4    NaN       0.0     1.0               NaN               NaN   

   Temp3_South_Less  Temp4_South_Less  Temp1_South_Gr  Temp2_South_Gr  \
0               NaN               NaN             NaN             NaN   
1               NaN               NaN             NaN             NaN   
2               NaN               NaN             NaN             NaN   
3               NaN               NaN             NaN             NaN   
4               NaN               NaN             NaN             NaN   

   Temp3_South_Gr  Temp4_South_Gr  id  
0             NaN             NaN   0  
1             NaN             NaN   0  
2             NaN             NaN   0  
3             NaN             NaN   0  
4             NaN             NaN   0

In [3]:
ts.plot().update_layout(height=350, width=1350).show()

# 2. Build the Forecast with  SES (20%)

You need to apply SES model for the ts.
You can use code from seminars or you can write down your own code using any python lib.

Forecast delay $h=1$ for all point in this task.

* 0) Forecast the ts with SES $\alpha=.1$.
* 1) Split the ts to 4 equal parts: find the best param $\alpha$ of SES for the based on 3-rd part of ts (e.g. if time series includes date from 01Jan2020 till 31Dec2020 then 3rd part will be from 1Jul2020 till 30Sep2020). Is the optimal value close to 0 or 1? (use MAPE as a loss function).
* 2) Draw the forecast that correspond to SES with optimial value $\alpha$
     Conclude whether SES can be used for this TS? If can not than explain why.
* 3) Calculate MAPE loss of the best forecast of the ts based on 4-th part of the ts.

---



In [13]:
start_date = pd.to_datetime('2011-01-01')
end_date = pd.to_datetime('2014-01-01')
total_days = (end_date - start_date).days

num_days_part_3 = int(3 * total_days / 4)
num_days_part_1 = total_days - num_days_part_3

end_1 = start_date + pd.Timedelta(days=num_days_part_3)
start_2  = start_date + pd.Timedelta(days=num_days_part_3)

print(end_1)
print(start_2)


2013-04-02 00:00:00
2013-04-02 00:00:00


In [15]:
train_ts = df[df.id == 0].drop(columns='id').set_index('Date')['2011-01-01':end_1]
test_ts = df[df.id == 0].drop(columns='id').set_index('Date')[start_2:'2014-01-01']

In [16]:
train_ts.plot().update_layout(height=350, width=1350).show()

In [17]:
test_ts.plot().update_layout(height=350, width=1350).show()

## 1) Search for the optimal $\alpha$

In [18]:
ALPHA = [0.9, 0.7, 0.4, 0.2, .15, 0.1, 0.05, 0.01, 0.001, 0.00001]
ESparams = [{'alpha':alpha} for alpha in ALPHA]
FRC_ts = build_forecast(h=1, ts=train_ts, alg_name = 'SimpleExponentialSmoothing', alg_title = 'SES', params = ESparams)

In [20]:
qlt_ses = pd.DataFrame(index = train_ts.columns, columns = FRC_ts.keys())

In [21]:
qlt_ses.columns

Index(['SES {'alpha': 0.9}', 'SES {'alpha': 0.7}', 'SES {'alpha': 0.4}',
       'SES {'alpha': 0.2}', 'SES {'alpha': 0.15}', 'SES {'alpha': 0.1}',
       'SES {'alpha': 0.05}', 'SES {'alpha': 0.01}', 'SES {'alpha': 0.001}',
       'SES {'alpha': 1e-05}'],
      dtype='object')

In [22]:
FRC_ts["SES {'alpha': 0.9}"].index

DatetimeIndex(['2011-01-01', '2011-01-02', '2011-01-03', '2011-01-04',
               '2011-01-05', '2011-01-06', '2011-01-07', '2011-01-08',
               '2011-01-09', '2011-01-10',
               ...
               '2013-03-25', '2013-03-26', '2013-03-27', '2013-03-28',
               '2013-03-29', '2013-03-30', '2013-03-31', '2013-04-01',
               '2013-04-02', '2013-04-03'],
              dtype='datetime64[ns]', length=824, freq=None)

In [24]:
# compare ES parameters
ix = ts.loc['2011-01-01':end_1].index
for param_cntr in sorted(qlt_ses.columns):
    frc_ts = FRC_ts[param_cntr]
    qlt_ses[param_cntr],_ = qualityMAPE(ts.loc[ix], frc_ts.loc[ix])

qlt_ses[qlt_ses.columns].mean().sort_values()

SES {'alpha': 0.9}      0.615982
SES {'alpha': 0.7}      0.637030
SES {'alpha': 0.4}      0.685488
SES {'alpha': 0.2}      0.756198
SES {'alpha': 0.15}     0.792640
SES {'alpha': 0.1}      0.850056
SES {'alpha': 0.05}     0.978442
SES {'alpha': 0.01}     1.285091
SES {'alpha': 0.001}    1.411389
SES {'alpha': 1e-05}    1.869259
dtype: float64

следовательно alpha = 0.9

## 2) draw the forecast with optimial value $\alpha $

In [10]:
alg_name = qlt_ses[qlt_ses.columns].mean().sort_values().index[0]
plot_ts_forecast(ts.loc['2011-01-01':'2014-01-01'], FRC_ts[alg_name].loc['2011-01-01':'2014-01-01']
               , ts_num=0, alg_title='SimpleExponentialSmoothing')

** Question**
    * Does SES follow to the TS components?

## 3) Calculate loss of the forecast of TS in 4th part of the time series

In [ ]:
quality???(ts.loc[???], FRC_ts[alg_name].loc[???])[0]

# 3. Winters model for Additive Seasonality (25%)
You need to realize ES model for TS with additive seasonality and then apply it to the ts.

You can use code from seminars or you can write down your own code using any python lib.


Forecast delay $h=1$ for all point in this task.

* 1) Realize Additive Winters model
* 2) Split the ts to 4 equal parts: find the best params $\alpha$ (smoothing of level) and $\gamma$ (smoothing of seasonality) for the based on 3-rd part of ts (e.g. if time series includes date from 01Jan2020 till 31Dec2020 then 3rd part will be from 1Jul2020 till 30Sep2020). Use MAPE as a loss function.
* 3) Draw the forecast that correspond optimal values $\alpha$ and $\gamma$ for the whole TS
* 4) Calculate MAPE loss of the best forecast of the ts based on 4-th part of the ts. Compare it with accuracy of SES: is it better?
* 5) Based on results of 3) and 4) conclude whether Additive Winter's ES is appropriate for this TS.

In [ ]:
# Start with this code
###################### Winters Exponential Smoothing #########################
# x <array Tx1>- time series,
# h <scalar> - forecasting delay
# Params <dict> - dictionary with
#    alpha <scalar in [0,1]> - smoothing parameter
#    delts <scalar in [0,1]> - seasonality smoothing parameter

def WintersExponentialSmoothing(x, h, Params):
    T = len(x)
    alpha = Params['alpha']
    gamma = Params['gamma']
    p = Params['seasonality_period']

    FORECAST = ## put foreast of the model here

    l= # initialize ts level
    s= # initalize seasonality values (it must be vector of lenth p)

    for cntr in range(T):
        if not math.isnan(x[cntr]):
            if math.isnan(l):
                l= # initialize

            if math.isnan(s[cntr % p]):
                s[cntr % p]= # initialize

            l = # recurrent smoothing of level
            s[cntr % p] = # recurrent smoothing of seasonality

        FORECAST[cntr+h] = ??
    return FORECAST

In [ ]:
# Put your code here


# 4. Theil-Wage model for TS with linear trend and seasonality (25%)
You need to realize Theil-Wage model and then use it for forecasting the ts.

You can use code from seminars or you can write down your own code using any python lib.


Forecast delay $h=1$ for all point in this task.

* 1) Realize Theil-Wage model
* 2) Split the ts to 4 equal parts: find the best params $\alpha$ (smoothing of level), $\beta$ (smoothing of trend) and $\gamma$ (smoothing of seasonality) for the based on 3-rd part of ts (e.g. if time series includes date from 01Jan2020 till 31Dec2020 then 3rd part will be from 1Jul2020 till 30Sep2020). Use MAPE as a loss function.
* 3) Draw forecast with optimal values $\alpha$, $\beta$ and $\gamma$
* 4) Calculate MAPE loss of the best forecast of the ts based on 4-th part of the ts. Compare it with accuracy of Additive Winters model: is it better than the last one?
* *5) Suggest how can the Theil-Wage model be improved to make accuracy of forecast better?

In [ ]:
# Put your code here

# 5. Non-additive model of ES (25%)
You need to realize some ES-model that include non-addive component (or multiplicative trend or multiplicative component) or/and damped-trend component and then use it for forecasting of the ts

You can use code from seminars or you can write down your own code using any python lib.

Forecast delay $h=1$ for all point in this task.

* 1) Realize one of following ES models: ESM(A,M) (t.e. Holt-Winters model), ESM(Ad,M), ESM(M,A), ESM(M,M), ESM(Md,M) model.
* 2) Split the ts to 4 equal parts: find the best params $\alpha$ (smoothing of level)/$\beta$ (smoothing of trend)/$\gamma$ (smoothing of seasonality) for the based on 3-rd part of ts (e.g. if time series includes date from 01Jan2020 till 31Dec2020 then 3rd part will be from 1Jul2020 till 30Sep2020). Use MAPE as a loss function.
Note: if you seelct damped trend model then you can set  $\phi$ value expertly (say $0.98$). (Loss function should be the same as in task 2.)
* 3) Draw forecast with optimal values of it's params.
* 4) Calculate accuracy of the forecast of TS based on 4-th part of the ts. Compare it with accuracy of Additive Winters model and Theil-Wage model, which model is the best?
* 5) Will be results the same if forecas horizon is different (h = seasonlaity period of data)? Please give reasons for your answer.

In [ ]:
# Put your code here